##**Printing best solution obtained after applying Genetic Algorithm**

In [ ]:
import random
from tabulate import tabulate

courses = ['CNET', 'TOA', 'SDA', 'AI', 'NCA','DB','OS','Algo','DBLab','OSLab', 'AILab', 'CNETLab']  # Including lab courses
classrooms = {'classroom': 60, 'large_hall': 120}
time_slots = ['8:30-9:50', '10:00-11:20', '11:30-12:50','1:00-2:20']
max_hours_per_day = 6
max_courses_per_professor = 3
max_courses_per_section = 5
break_time = 15  # in minutes
lab_slots = [['2:30-3:50', '3:55-5:15']]  # Lab lectures should be conducted in two consecutive slots
conflicts = [('C1', 'C2', 10), ('C1', 'C4', 5), ('C2', 'C5', 7), ('C3', 'C4', 12), ('C4', 'C5', 8)]

def random_solution():
    solution = []
    professors_courses = {
        "professor" + str(i): {"theory": [], "lab": []} for i in range(1, 15)
    }
    sections_courses = {section: 0 for section in ["A", "B", "C", "D", "E"]}

    for course in courses:
        # Determine if the course is theory or lab
        if course.endswith("Lab"):
            theory_lab = "Lab"
            timeslots = lab_slots
            # Choose a lab professor
            available_professors = [
                p for p, courses in professors_courses.items() if not courses["lab"]
            ]
            professor = random.choice(available_professors)
            professors_courses[professor]["lab"].append(course)
        else:
            theory_lab = "Theory"
            timeslots = [["T1", "T2"], ["T2", "T3"]]
            # Choose a theory professor
            available_professors = [
                p for p, courses in professors_courses.items() if not courses["theory"]
            ]
            professor = random.choice(available_professors)
            professors_courses[professor]["theory"].append(course)

        section = random.choice(list(sections_courses.keys()))
        section_strength = random.randint(20, 100)  # Random section strength between 20 and 100

        while sections_courses[section] >= max_courses_per_section:
            section = random.choice(list(sections_courses.keys()))
        sections_courses[section] += 1

        # Choose room based on section strength
        if section_strength <= 60:
            classroom = "classroom"
        else:
            classroom = "large_hall"

        # Ensure theory classes in the morning and lab in the afternoon
        if theory_lab == "Theory":  # Theory class
            day = random.randint(1, 3)  # Morning sessions on days 1-3
        else:  # Lab class
            day = random.randint(4, 5)  # Afternoon sessions on days 4-5

        timeslot = random.choice(timeslots)
        room_size = classrooms[classroom]

        solution.append(
            (
                course,
                theory_lab,
                section,
                section_strength,
                professor,
                day,
                timeslot[0],
                classroom,
                room_size,
                day,
                timeslot[1],
                classroom,
                room_size,
            )
        )

    return solution

def is_valid_solution(solution):
    # Check if a professor is assigned two different lectures at the same time
    professors_schedule = {}
    for entry in solution:
        course, _, _, _, professor, day, timeslot, _, _, _, _, _, _ = entry
        if professor in professors_schedule:
            if (day, timeslot) in professors_schedule[professor]:
                return False
            else:
                professors_schedule[professor].append((day, timeslot))
        else:
            professors_schedule[professor] = [(day, timeslot)]

    # Check if the same section is assigned to two different rooms at the same time
    sections_schedule = {}
    for entry in solution:
        _, _, section, _, _, day, timeslot, _, _, _, _, _, _ = entry
        if section in sections_schedule:
            if (day, timeslot) in sections_schedule[section]:
                return False
            else:
                sections_schedule[section].append((day, timeslot))
        else:
            sections_schedule[section] = [(day, timeslot)]

    # Check if a room is assigned for two different sections at the same time
    rooms_schedule = {}
    for entry in solution:
        _, _, _, _, _, day, timeslot, room, _, _, _, _, _ = entry
        if room in rooms_schedule:
            if (day, timeslot) in rooms_schedule[room]:
                return False
            else:
                rooms_schedule[room].append((day, timeslot))
        else:
            rooms_schedule[room] = [(day, timeslot)]

    # Ensure no section has more than 5 courses in a semester
    section_courses_count = {section: 0 for section in ['A', 'B', 'C', 'D', 'E']}
    for entry in solution:
        _, _, section, _, _, _, _, _, _, _, _, _, _ = entry
        section_courses_count[section] += 1
        if section_courses_count[section] > max_courses_per_section:
            return False

    return True


def fitness(solution):
    score = 0

    # Check if solution violates hard constraints and penalize accordingly
    if not is_valid_solution(solution):
        score += 1000  # A large penalty for violating hard constraints

    # Soft Constraints
    # Ensure same classroom is used throughout the week
    for course in courses:
        classrooms_assigned = set()
        for entry in solution:
            if entry[0] == course:
                classroom = entry[7]
                if classroom in classrooms_assigned:
                    score -= 10  # Penalize for changing classrooms during the week
                else:
                    classrooms_assigned.add(classroom)

    # Additional soft constraints scoring implemented here
    # Ensure theory classes in the morning and lab in the afternoon
    for entry in solution:
        course, theory_lab, _, _, _, day, timeslot, _, _, _, _, _, _ = entry
        if theory_lab == "Theory" and day > 3:
            score -= 10  # Penalize for theory classes in the afternoon
        elif theory_lab == "Lab" and day < 4:
            score -= 10  # Penalize for lab classes in the morning

    # Ensure no two theory classes are scheduled at the same time
    theory_classes = [entry for entry in solution if entry[1] == "Theory"]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][6] == theory_classes[j][6]:
                score -= 10  # Penalize for two theory classes at the same time

    # Ensure no two lab classes are scheduled at the same time
    lab_classes = [entry for entry in solution if entry[1] == "Lab"]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][6] == lab_classes[j][6]:
                score -= 10  # Penalize for two lab classes at the same time

    # Ensure no two theory classes are scheduled in the same room at the same time
    theory_classes = [entry for entry in solution if entry[1] == "Theory"]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7]:
                score -= 10  # Penalize for two theory classes in the same room at the same time

    # Ensure no two lab classes are scheduled in the same room at the same time
    lab_classes = [entry for entry in solution if entry[1] == "Lab"]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7]:
                score -= 10  # Penalize for two lab classes in the same room at the same time

    # Ensure no two theory classes are scheduled in the same room on the same day
    theory_classes = [entry for entry in solution if entry[1] == "Theory"]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7]:
                score -= 10  # Penalize for two theory classes in the same room on the same day

    # Ensure no two lab classes are scheduled in the same room on the same day
    lab_classes = [entry for entry in solution if entry[1] == "Lab"]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7]:
                score -= 10  # Penalize for two lab classes in the same room on the same day

    # Ensure no two theory classes are scheduled in the same room in consecutive slots
    theory_classes = [entry for entry in solution if entry[1] == "Theory"]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7] and theory_classes[i][6] == 'T1' and theory_classes[j][6] == 'T2':
                score -= 10  # Penalize for two theory classes in the same room in consecutive slots

    # Ensure no two lab classes are scheduled in the same room in consecutive slots
    lab_classes = [entry for entry in solution if entry[1] == "Lab"]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7] and lab_classes[i][6] == 'T1' and lab_classes[j][6] == 'T2':
                score -= 10  # Penalize for two lab classes in the same room in consecutive slots

    # Ensure no two theory classes are scheduled in the same room with a break in between
    theory_classes = [entry for entry in solution if entry[1] == "Theory"]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7] and theory_classes[i][6] == 'T1' and theory_classes[j][6] == 'T3':
                score -= 10  # Penalize for two theory classes in the same room with a break in between

    # Ensure no two lab classes are scheduled in the same room with a break in between
    lab_classes = [entry for entry in solution if entry[1] == "Lab"]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7] and lab_classes[i][6] == 'T1' and lab_classes[j][6] == 'T3':
                score -= 10  # Penalize for two lab classes in the same room with a break in between

    return -score  # Inverse of the sum of all conflicts/clashes and penalties


def genetic_algorithm(population_size, num_generations, selection_rate, mutation_rate):
    population = [random_solution() for _ in range(population_size)]

    for _ in range(num_generations):

        # Evaluate fitness scores for the population
        fitness_scores = [fitness(solution) for solution in population]

        # Select parents for reproduction
        num_parents = int(selection_rate * population_size)
        parents = [population[i] for i in sorted(random.sample(range(population_size), num_parents), reverse=True, key=lambda x: fitness_scores[x])]

        offspring = []

        # Generate offspring through crossover and mutation
        for _ in range(population_size - num_parents):
            parent1 = random.choice(parents)
            parent2 = random.choice(parents)
            crossover_point = random.randint(1, len(courses) - 1)
            child = parent1[:crossover_point] + parent2[crossover_point:]

            # Apply mutation
            for i in range(len(child)):
                if random.uniform(0, 1) < mutation_rate:
                    child[i] = (child[i][0], random.choice(["Theory", "Lab"]), child[i][2], child[i][3], child[i][4], random.randint(1, 5), random.choice(time_slots), child[i][7], child[i][8], random.randint(1, 5), random.choice(time_slots), child[i][11], child[i][12])

            offspring.append(child)

        # Update population with offspring
        population = parents + offspring

    # Select the best solution from the final population
    fitness_scores = [fitness(solution) for solution in population]
    best_solution = population[fitness_scores.index(max(fitness_scores))]
    return best_solution

best_solution = genetic_algorithm(population_size=100, num_generations=1000, selection_rate=0.4, mutation_rate=0.1)
print("Best Solution:")
print(best_solution)
print("Fitness Score:")
print(fitness(best_solution))

def print_solution(solution):
    headers = ["Course", "Theory/Lab", "Section", "Section Strength", "Professor", "First Lecture Day", "First Lecture Timeslot", "First Lecture Room", "First Lecture Room Size", "Second Lecture Day", "Second Lecture Timeslot", "Second Lecture Room", "Second Lecture Room Size"]
    table_data = []
    day_mapping = {1: "Mon", 2: "Tue", 3: "Wed", 4: "Thu", 5: "Fri"}
    room_count = {}

    for entry in solution:
        entry_list = list(entry)
        # Convert numerical day to weekday
        entry_list[5] = day_mapping[entry_list[5]]
        entry_list[9] = day_mapping[entry_list[9]]

        # Assign unique room names or numbers
        room = entry_list[7]
        room_size = entry_list[8]
        if room in room_count:
            room_count[room] += 1
        else:
            room_count[room] = 1
        entry_list[7] = f"Room {room_count[room]} ({room})"

        # Ensure no two classes are in the same room
        second_room = entry_list[11]
        second_room_size = entry_list[12]
        if second_room in room_count:
            room_count[second_room] += 1
        else:
            room_count[second_room] = 1
        entry_list[11] = f"Room {room_count[second_room]} ({second_room})"

        table_data.append(entry_list)

    print(tabulate(table_data, headers=headers, tablefmt="grid", colalign=("center", "center", "center", "center", "center", "center", "center", "center", "center", "center", "center", "center", "center")))

print_solution(best_solution)


Best Solution:
[('CNET', 'Theory', 'C', 57, 'professor11', 2, '11:30-12:50', 'classroom', 60, 4, '8:30-9:50', 'classroom', 60), ('TOA', 'Lab', 'E', 81, 'professor1', 3, '10:00-11:20', 'large_hall', 120, 5, '8:30-9:50', 'large_hall', 120), ('SDA', 'Lab', 'D', 73, 'professor13', 3, '1:00-2:20', 'large_hall', 120, 3, '1:00-2:20', 'large_hall', 120), ('AI', 'Lab', 'A', 55, 'professor3', 5, '8:30-9:50', 'classroom', 60, 5, '8:30-9:50', 'classroom', 60), ('NCA', 'Lab', 'C', 82, 'professor7', 4, '8:30-9:50', 'large_hall', 120, 1, '10:00-11:20', 'large_hall', 120), ('DB', 'Theory', 'B', 87, 'professor4', 2, '8:30-9:50', 'large_hall', 120, 5, '1:00-2:20', 'large_hall', 120), ('OS', 'Lab', 'A', 38, 'professor9', 5, '11:30-12:50', 'classroom', 60, 4, '8:30-9:50', 'classroom', 60), ('Algo', 'Lab', 'C', 55, 'professor7', 4, '11:30-12:50', 'classroom', 60, 1, '11:30-12:50', 'classroom', 60), ('DBLab', 'Lab', 'A', 47, 'professor13', 5, '10:00-11:20', 'classroom', 60, 4, '8:30-9:50', 'classroom', 60),

________________________________________________________________________________________________________________

## **Printing all valid Solutions** (It takes too much time and many solutions are printed)

-------------------------------------------------------------------------------------------------------------------

In [ ]:
import random
from tabulate import tabulate

courses = ['CNET', 'TOA', 'SDA', 'AI', 'NCA', 'AILab', 'CNETLab']  # Including lab courses
classrooms = {'classroom': 60, 'large_hall': 120}
time_slots = ['8:30-9:50', '10:00-11:20', '11:30-12:50','1:00-2:20']
max_hours_per_day = 6
max_courses_per_professor = 3
max_courses_per_section = 5
break_time = 15  # in minutes
lab_slots = [['2:30-3:50', '3:55-5:15']]  # Lab lectures should be conducted in two consecutive slots
conflicts = [('C1', 'C2', 10), ('C1', 'C4', 5), ('C2', 'C5', 7), ('C3', 'C4', 12), ('C4', 'C5', 8)]

def random_solution():
    solution = []
    professors_courses = {"professor" + str(random.randint(1, 7)): course for course in courses}
    sections_courses = {section: 0 for section in range(1, 6)}

    for course in courses:
        # Determine if the course is theory or lab
        if course.endswith('L'):
            theory_lab = 1  # Lab
            timeslots = lab_slots
            # Choose a lab professor
            professor = random.choice([p for p in professors_courses.keys() if "Lab" in p])
        else:
            theory_lab = 0  # Theory
            timeslots = [['T1', 'T2'], ['T2', 'T3']]
            # Choose a theory professor
            professor = random.choice([p for p in professors_courses.keys() if "Lab" not in p])

        section = random.randint(1, 5)
        section_strength = random.randint(20, 30)  # Dummy values

        while sections_courses[section] >= max_courses_per_section:
            section = random.randint(1, 5)
        sections_courses[section] += 1

        # Ensure same classroom is used throughout the week
        classroom = random.choice(list(classrooms.keys()))

        # Ensure theory classes in the morning and lab in the afternoon
        if theory_lab == 0:  # Theory class
            day = random.randint(1, 3)  # Morning sessions on days 1-3
        else:  # Lab class
            day = random.randint(4, 5)  # Afternoon sessions on days 4-5

        timeslot = random.choice(timeslots)
        room_size = classrooms[classroom]

        solution.append((course, theory_lab, section, section_strength, professor,
                         day, timeslot[0], classroom, room_size,
                         day, timeslot[1], classroom, room_size))
    return solution

def is_valid_solution(solution):
    # Check if a professor is assigned two different lectures at the same time
    professors_schedule = {}
    for entry in solution:
        course, _, _, _, professor, day, timeslot, _, _, _, _, _, _ = entry
        if professor in professors_schedule:
            if (day, timeslot) in professors_schedule[professor]:
                return False
            else:
                professors_schedule[professor].append((day, timeslot))
        else:
            professors_schedule[professor] = [(day, timeslot)]

    # Check if the same section is assigned to two different rooms at the same time
    sections_schedule = {}
    for entry in solution:
        _, _, section, _, _, day, timeslot, _, _, _, _, _, _ = entry
        if section in sections_schedule:
            if (day, timeslot) in sections_schedule[section]:
                return False
            else:
                sections_schedule[section].append((day, timeslot))
        else:
            sections_schedule[section] = [(day, timeslot)]

    # Check if a room is assigned for two different sections at the same time
    rooms_schedule = {}
    for entry in solution:
        _, _, _, _, _, day, timeslot, room, _, _, _, _, _ = entry
        if room in rooms_schedule:
            if (day, timeslot) in rooms_schedule[room]:
                return False
            else:
                rooms_schedule[room].append((day, timeslot))
        else:
            rooms_schedule[room] = [(day, timeslot)]

    return True

def fitness(solution):
    score = 0

    # Check if solution violates hard constraints and penalize accordingly
    if not is_valid_solution(solution):
        score += 1000  # A large penalty for violating hard constraints

    # Soft Constraints
    # Ensure same classroom is used throughout the week
    for course in courses:
        classrooms_assigned = set()
        for entry in solution:
            if entry[0] == course:
                classroom = entry[7]
                if classroom in classrooms_assigned:
                    score -= 10  # Penalize for changing classrooms during the week
                else:
                    classrooms_assigned.add(classroom)

    # Additional soft constraints scoring here implement
    # Ensure theory classes in the morning and lab in the afternoon
    for entry in solution:
        course, theory_lab, _, _, _, day, timeslot, _, _, _, _, _, _ = entry
        if theory_lab == 0 and day > 3:
            score -= 10  # Penalize for theory classes in the afternoon
        elif theory_lab == 1 and day < 4:
            score -= 10  # Penalize for lab classes in the morning

    # Ensure no two theory classes are scheduled at the same time
    theory_classes = [entry for entry in solution if entry[1] == 0]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][6] == theory_classes[j][6]:
                score -= 10  # Penalize for two theory classes at the same time

    # Ensure no two lab classes are scheduled at the same time
    lab_classes = [entry for entry in solution if entry[1] == 1]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][6] == lab_classes[j][6]:
                score -= 10  # Penalize for two lab classes at the same time

    # Ensure no two theory classes are scheduled in the same room at the same time
    theory_classes = [entry for entry in solution if entry[1] == 0]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][6] == theory_classes[j][6] and theory_classes[i][7] == theory_classes[j][7]:
                score -= 10  # Penalize for two theory classes in the same room at the same time

    # Ensure no two lab classes are scheduled in the same room at the same time
    lab_classes = [entry for entry in solution if entry[1] == 1]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][6] == lab_classes[j][6] and lab_classes[i][7] == lab_classes[j][7]:
                score -= 10  # Penalize for two lab classes in the same room at the same time

    # Ensure no two theory classes are scheduled in the same room on the same day
    theory_classes = [entry for entry in solution if entry[1] == 0]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7]:
                score -= 10  # Penalize for two theory classes in the same room on the same day

    # Ensure no two lab classes are scheduled in the same room on the same day
    lab_classes = [entry for entry in solution if entry[1] == 1]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7]:
                score -= 10  # Penalize for two lab classes in the same room on the same day

    # Ensure no two theory classes are scheduled in the same room in consecutive slots
    theory_classes = [entry for entry in solution if entry[1] == 0]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7] and theory_classes[i][6] == 'T1' and theory_classes[j][6] == 'T2':
                score -= 10  # Penalize for two theory classes in the same room in consecutive slots

    # Ensure no two lab classes are scheduled in the same room in consecutive slots
    lab_classes = [entry for entry in solution if entry[1] == 1]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7] and lab_classes[i][6] == 'T1' and lab_classes[j][6] == 'T2':
                score -= 10  # Penalize for two lab classes in the same room in consecutive slots

    # Ensure no two theory classes are scheduled in the same room with a break in between
    theory_classes = [entry for entry in solution if entry[1] == 0]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7] and theory_classes[i][6] == 'T1' and theory_classes[j][6] == 'T3':
                score -= 10  # Penalize for two theory classes in the same room with a break in between

    # Ensure no two lab classes are scheduled in the same room with a break in between
    lab_classes = [entry for entry in solution if entry[1] == 1]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7] and lab_classes[i][6] == 'T1' and lab_classes[j][6] == 'T3':
                score -= 10  # Penalize for two lab classes in the same room with a break in between

    return -score  # Inverse of the sum of all conflicts/clashes and penalties


def genetic_algorithm(population_size, num_generations, selection_rate, mutation_rate):
    population = [random_solution() for _ in range(population_size)]
    valid_solutions = []  # Store all valid solutions

    for _ in range(num_generations):

        # Evaluate fitness scores for the population
        fitness_scores = [fitness(solution) for solution in population]

        # Select parents for reproduction
        num_parents = int(selection_rate * population_size)
        parents = [population[i] for i in sorted(random.sample(range(population_size), num_parents), reverse=True, key=lambda x: fitness_scores[x])]

        offspring = []

        # Generate offspring through crossover and mutation
        for _ in range(population_size - num_parents):
            parent1 = random.choice(parents)
            parent2 = random.choice(parents)
            crossover_point = random.randint(1, len(courses) - 1)
            child = parent1[:crossover_point] + parent2[crossover_point:]

            # Apply mutation
            for i in range(len(child)):
                if random.uniform(0, 1) < mutation_rate:
                    child[i] = (child[i][0], random.randint(0, 1), child[i][2], child[i][3], child[i][4], random.randint(1, 5), random.choice(time_slots), child[i][7], child[i][8], random.randint(1, 5), random.choice(time_slots), child[i][11], child[i][12])

            offspring.append(child)

        # Update population with offspring
        population = parents + offspring

        # Store valid solutions
        valid_solutions.extend([solution for solution in population if is_valid_solution(solution)])

    # Select the best solution from the final population
    fitness_scores = [fitness(solution) for solution in valid_solutions]
    best_solution = valid_solutions[fitness_scores.index(max(fitness_scores))]
    return best_solution, valid_solutions

best_solution, all_valid_solutions = genetic_algorithm(population_size=100, num_generations=1000, selection_rate=0.4, mutation_rate=0.1)

print("All Valid Solutions:")
for i, solution in enumerate(all_valid_solutions):
    print(f"Solution {i+1}:")
    print_solution(solution)
    print("\n")

print("Best Solution:")
print_solution(best_solution)
print("Fitness Score:")
print(fitness(best_solution))


Streaming output truncated to the last 5000 lines.
+----------+--------------+-----------+--------------------+-------------+---------------------+--------------------------+----------------------+---------------------------+----------------------+---------------------------+-----------------------+----------------------------+
|  Course  |  Theory/Lab  |  Section  |  Section Strength  |  Professor  |  First Lecture Day  |  First Lecture Timeslot  |  First Lecture Room  |  First Lecture Room Size  |  Second Lecture Day  |  Second Lecture Timeslot  |  Second Lecture Room  |  Second Lecture Room Size  |
+==========+==============+===========+====================+=============+=====================+==========================+======================+===========================+======================+===========================+=======================+============================+
|   CNET   |      0       |     2     |         27         | professor3  |         Thu         |       10:00-11:

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.

Solution 1700:
+----------+--------------+-----------+--------------------+-------------+---------------------+--------------------------+----------------------+---------------------------+----------------------+---------------------------+-----------------------+----------------------------+
|  Course  |  Theory/Lab  |  Section  |  Section Strength  |  Professor  |  First Lecture Day  |  First Lecture Timeslot  |  First Lecture Room  |  First Lecture Room Size  |  Second Lecture Day  |  Second Lecture Timeslot  |  Second Lecture Room  |  Second Lecture Room Size  |
+==========+==============+===========+====================+=============+=====================+==========================+======================+===========================+======================+===========================+=======================+============================+
|   CNET   |      1       |     2     |         27         | professor3  |         Wed         |

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
Solution 2557:
+----------+--------------+-----------+--------------------+-------------+---------------------+--------------------------+----------------------+---------------------------+----------------------+---------------------------+-----------------------+----------------------------+
|  Course  |  Theory/Lab  |  Section  |  Section Strength  |  Professor  |  First Lecture Day  |  First Lecture Timeslot  |  First Lecture Room  |  First Lecture Room Size  |  Second Lecture Day  |  Second Lecture Timeslot  |  Second Lecture Room  |  Second Lecture Room Size  |
+==========+==============+===========+====================+=============+=====================+==========================+======================+===========================+======================+===========================+=======================+============================+
|   CNET   |      1       |     5     |         25         | professor5  |         Mon         | 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
+----------+--------------+-----------+--------------------+-------------+---------------------+--------------------------+----------------------+---------------------------+----------------------+---------------------------+-----------------------+----------------------------+
|  Course  |  Theory/Lab  |  Section  |  Section Strength  |  Professor  |  First Lecture Day  |  First Lecture Timeslot  |  First Lecture Room  |  First Lecture Room Size  |  Second Lecture Day  |  Second Lecture Timeslot  |  Second Lecture Room  |  Second Lecture Room Size  |
+==========+==============+===========+====================+=============+=====================+==========================+======================+===========================+======================+===========================+=======================+============================+
|   CNET   |      0       |     2     |         27         | professor3  |         Thu         |        8:30-9:5

KeyboardInterrupt: 

##TRY FOR ENCODING

In [ ]:
import random
from tabulate import tabulate

courses = ['CNET', 'TOA', 'SDA', 'AI', 'NCA', 'AILab', 'CNETLab']  # Including lab courses
classrooms = {'classroom': 60, 'large_hall': 120}
time_slots = ['8:30-9:50', '10:00-11:20', '11:30-12:50', '1:00-2:20', 'T1', 'T2', 'T3']


max_hours_per_day = 6
max_courses_per_professor = 3
max_courses_per_section = 5
break_time = 15  # in minutes
lab_slots = [['2:30-3:50', '3:55-5:15']]  # Lab lectures should be conducted in two consecutive slots
conflicts = [('C1', 'C2', 10), ('C1', 'C4', 5), ('C2', 'C5', 7), ('C3', 'C4', 12), ('C4', 'C5', 8)]

# Binary encoding lengths for each attribute of a course entry
encoding_lengths = {
    "Course": len(bin(len(courses) - 1)[2:]),  # Length of binary encoding for courses
    "Theory/Lab": 1,  # Binary encoding for theory/lab flag (0 or 1)
    "Section": len(bin(len(["A", "B", "C", "D", "E"]) - 1)[2:]),  # Length of binary encoding for sections
    "Section Strength": 6,  # Adjust this value as needed based on the range of section strengths
    "Professor": len(bin(7)[2:]),  # Length of binary encoding for professors (7 professors)
    "Day": len(bin(5)[2:]),  # Length of binary encoding for days (5 days)
    "Timeslot": len(bin(len(time_slots) - 1)[2:]),  # Length of binary encoding for timeslots
    "Room Size": len(bin(max(classrooms.values()))[2:])  # Length of binary encoding for room size
}




def binary_encode(value, length):
    """
    Encode an integer value into binary string of specified length.
    """
    binary_string = bin(value)[2:]
    padded_binary_string = binary_string.zfill(length)
    return padded_binary_string


def random_solution():
    courses = ['CNET', 'TOA', 'SDA', 'AI', 'NCA', 'AILab', 'CNETLab']  # Including lab courses
    classrooms = {'classroom': 60, 'large_hall': 120}
    time_slots = ['8:30-9:50', '10:00-11:20', '11:30-12:50', '1:00-2:20', '2:30-3:50', '3:55-5:15']  # Including lab time slots
    max_hours_per_day = 6
    max_courses_per_professor = 3
    max_courses_per_section = 5
    break_time = 15  # in minutes
    lab_slots = [['2:30-3:50', '3:55-5:15']]  # Lab lectures should be conducted in two consecutive slots
    conflicts = [('C1', 'C2', 10), ('C1', 'C4', 5), ('C2', 'C5', 7), ('C3', 'C4', 12), ('C4', 'C5', 8)]

    sections = ["A", "B", "C", "D", "E"]  # Define sections

    solution = []
    professors_courses = {
        "professor" + str(i): {"theory": [], "lab": []} for i in range(1, 8)
    }
    sections_courses = {section: 0 for section in sections}

    for course in courses:
        # Determine if the course is theory or lab
        if course.endswith("Lab"):
            theory_lab = 1  # Lab
            timeslots = lab_slots
            # Choose a lab professor
            available_professors = [
                p for p, courses in professors_courses.items() if not courses["lab"]
            ]
            professor = random.choice(available_professors)
            professors_courses[professor]["lab"].append(course)
        else:
            theory_lab = 0  # Theory
            timeslots = [['T1', 'T2'], ['T2', 'T3']]
            # Choose a theory professor
            available_professors = [
                p for p, courses in professors_courses.items() if not courses["theory"]
            ]
            professor = random.choice(available_professors)
            professors_courses[professor]["theory"].append(course)

        section = random.choice(sections)
        section_strength = random.randint(20, 30)  # Dummy values

        while sections_courses[section] >= max_courses_per_section:
            section = random.choice(sections)
        sections_courses[section] += 1

        # Ensure same classroom is used throughout the week
        classroom = random.choice(list(classrooms.keys()))

        # Ensure theory classes in the morning and lab in the afternoon
        if theory_lab == 0:  # Theory class
            day = random.randint(1, 3)  # Morning sessions on days 1-3
        else:  # Lab class
            day = random.randint(4, 5)  # Afternoon sessions on days 4-5

        timeslot = random.choice(timeslots)
        room_size = classrooms[classroom]

        solution.append(
            (
                binary_encode(courses.index(course), encoding_lengths["Course"]),
                binary_encode(theory_lab, encoding_lengths["Theory/Lab"]),
                binary_encode(sections.index(section), encoding_lengths["Section"]),
                binary_encode(section_strength, encoding_lengths["Section Strength"]),
                binary_encode(int(professor[-1]), encoding_lengths["Professor"]),
                binary_encode(day, encoding_lengths["Day"]),
                binary_encode(time_slots.index(timeslot[0]), encoding_lengths["Timeslot"]),
                binary_encode(classrooms[classroom], encoding_lengths["Room Size"]),
                binary_encode(day, encoding_lengths["Day"]),
                binary_encode(time_slots.index(timeslot[1]), encoding_lengths["Timeslot"]),
                binary_encode(classrooms[classroom], encoding_lengths["Room Size"]),
            )
        )

    return solution




def is_valid_solution(solution):
    # Check if a professor is assigned two different lectures at the same time
    professors_schedule = {}
    for entry in solution:
        course, _, _, _, professor, day, timeslot, _, _, _, _, _, _ = entry
        if professor in professors_schedule:
            if (day, timeslot) in professors_schedule[professor]:
                return False
            else:
                professors_schedule[professor].append((day, timeslot))
        else:
            professors_schedule[professor] = [(day, timeslot)]

    # Check if the same section is assigned to two different rooms at the same time
    sections_schedule = {}
    for entry in solution:
        _, _, section, _, _, day, timeslot, _, _, _, _, _, _ = entry
        if section in sections_schedule:
            if (day, timeslot) in sections_schedule[section]:
                return False
            else:
                sections_schedule[section].append((day, timeslot))
        else:
            sections_schedule[section] = [(day, timeslot)]

    # Check if a room is assigned for two different sections at the same time
    rooms_schedule = {}
    for entry in solution:
        _, _, _, _, _, day, timeslot, room, _, _, _, _, _ = entry
        if room in rooms_schedule:
            if (day, timeslot) in rooms_schedule[room]:
                return False
            else:
                rooms_schedule[room].append((day, timeslot))
        else:
            rooms_schedule[room] = [(day, timeslot)]

    # Ensure no section has more than 5 courses in a semester
    section_courses_count = {section: 0 for section in ['A', 'B', 'C', 'D', 'E']}
    for entry in solution:
        _, _, section, _, _, _, _, _, _, _, _, _, _ = entry
        section_courses_count[section] += 1
        if section_courses_count[section] > max_courses_per_section:
            return False

    return True


def fitness(solution):
    score = 0

    # Check if solution violates hard constraints and penalize accordingly
    if not is_valid_solution(solution):
        score += 1000  # A large penalty for violating hard constraints

    # Soft Constraints
    # Ensure same classroom is used throughout the week
    for course in courses:
        classrooms_assigned = set()
        for entry in solution:
            if entry[0] == course:
                classroom = entry[7]
                if classroom in classrooms_assigned:
                    score -= 10  # Penalize for changing classrooms during the week
                else:
                    classrooms_assigned.add(classroom)

    # Additional soft constraints scoring here implement
    # Ensure theory classes in the morning and lab in the afternoon
    for entry in solution:
        course, theory_lab, _, _, _, day, timeslot, _, _, _, _, _, _ = entry
        if theory_lab == 0 and day > 3:
            score -= 10  # Penalize for theory classes in the afternoon
        elif theory_lab == 1 and day < 4:
            score -= 10  # Penalize for lab classes in the morning

    # Ensure no two theory classes are scheduled at the same time
    theory_classes = [entry for entry in solution if entry[1] == 0]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][6] == theory_classes[j][6]:
                score -= 10  # Penalize for two theory classes at the same time

    # Ensure no two lab classes are scheduled at the same time
    lab_classes = [entry for entry in solution if entry[1] == 1]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][6] == lab_classes[j][6]:
                score -= 10  # Penalize for two lab classes at the same time

    # Ensure no two theory classes are scheduled in the same room at the same time
    theory_classes = [entry for entry in solution if entry[1] == 0]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7]:
                score -= 10  # Penalize for two theory classes in the same room at the same time

    # Ensure no two lab classes are scheduled in the same room at the same time
    lab_classes = [entry for entry in solution if entry[1] == 1]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7]:
                score -= 10  # Penalize for two lab classes in the same room at the same time

    # Ensure no two theory classes are scheduled in the same room on the same day
    theory_classes = [entry for entry in solution if entry[1] == 0]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7]:
                score -= 10  # Penalize for two theory classes in the same room on the same day

    # Ensure no two lab classes are scheduled in the same room on the same day
    lab_classes = [entry for entry in solution if entry[1] == 1]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7]:
                score -= 10  # Penalize for two lab classes in the same room on the same day

    # Ensure no two theory classes are scheduled in the same room in consecutive slots
    theory_classes = [entry for entry in solution if entry[1] == 0]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7] and theory_classes[i][6] == 'T1' and theory_classes[j][6] == 'T2':
                score -= 10  # Penalize for two theory classes in the same room in consecutive slots

    # Ensure no two lab classes are scheduled in the same room in consecutive slots
    lab_classes = [entry for entry in solution if entry[1] == 1]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7] and lab_classes[i][6] == 'T1' and lab_classes[j][6] == 'T2':
                score -= 10  # Penalize for two lab classes in the same room in consecutive slots

    # Ensure no two theory classes are scheduled in the same room with a break in between
    theory_classes = [entry for entry in solution if entry[1] == 0]
    for i in range(len(theory_classes)):
        for j in range(i + 1, len(theory_classes)):
            if theory_classes[i][5] == theory_classes[j][5] and theory_classes[i][7] == theory_classes[j][7] and theory_classes[i][6] == 'T1' and theory_classes[j][6] == 'T3':
                score -= 10  # Penalize for two theory classes in the same room with a break in between

    # Ensure no two lab classes are scheduled in the same room with a break in between
    lab_classes = [entry for entry in solution if entry[1] == 1]
    for i in range(len(lab_classes)):
        for j in range(i + 1, len(lab_classes)):
            if lab_classes[i][5] == lab_classes[j][5] and lab_classes[i][7] == lab_classes[j][7] and lab_classes[i][6] == 'T1' and lab_classes[j][6] == 'T3':
                score -= 10  # Penalize for two lab classes in the same room with a break in between

    return -score  # Inverse of the sum of all conflicts/clashes and penalties


def genetic_algorithm(population_size, num_generations, selection_rate, mutation_rate):
    population = [random_solution() for _ in range(population_size)]

    for _ in range(num_generations):

        # Evaluate fitness scores for the population
        fitness_scores = [fitness(solution) for solution in population]

        # Select parents for reproduction
        num_parents = int(selection_rate * population_size)
        parents = [population[i] for i in sorted(random.sample(range(population_size), num_parents), reverse=True, key=lambda x: fitness_scores[x])]

        offspring = []

        # Generate offspring through crossover and mutation
        for _ in range(population_size - num_parents):
            parent1 = random.choice(parents)
            parent2 = random.choice(parents)
            crossover_point = random.randint(1, len(courses) - 1)
            child = parent1[:crossover_point] + parent2[crossover_point:]

            # Apply mutation
            for i in range(len(child)):
                if random.uniform(0, 1) < mutation_rate:
                    mutated_child = list(child[i])
                    for j in range(len(mutated_child)):
                        if isinstance(mutated_child[j], str):
                            mutated_child[j] = binary_encode(int(mutated_child[j], 2), encoding_lengths[list(encoding_lengths.keys())[j]])
                    child[i] = tuple(mutated_child)

            offspring.append(child)

        # Update population with offspring
        population = parents + offspring

    # Select the best solution from the final population
    fitness_scores = [fitness(solution) for solution in population]
    best_solution = population[fitness_scores.index(max(fitness_scores))]
    return best_solution

best_solution = genetic_algorithm(population_size=100, num_generations=1000, selection_rate=0.4, mutation_rate=0.1)
print("Best Solution:")
print(best_solution)
print("Fitness Score:")
print(fitness(best_solution))

def print_solution(solution):
    headers = ["Course", "Theory/Lab", "Section", "Section Strength", "Professor", "First Lecture Day", "First Lecture Timeslot", "First Lecture Room", "First Lecture Room Size", "Second Lecture Day", "Second Lecture Timeslot", "Second Lecture Room", "Second Lecture Room Size"]
    table_data = []
    day_mapping = {1: "Mon", 2: "Tue", 3: "Wed", 4: "Thu", 5: "Fri"}
    room_count = {}

    for entry in solution:
        entry_list = list(entry)
        # Convert numerical day to weekday
        entry_list[5] = day_mapping[int(entry_list[5], 2) + 1]
        entry_list[9] = day_mapping[int(entry_list[9], 2) + 1]

        # Assign unique room names or numbers
        room = entry_list[7]
        room_size = entry_list[8]
        if room in room_count:
            room_count[room] += 1
        else:
            room_count[room] = 1
        entry_list[7] = f"Room {room_count[room]} ({room})"

        # Ensure no two classes are in the same room
        second_room = entry_list[11]
        second_room_size = entry_list[12]
        if second_room in room_count:
            room_count[second_room] += 1
        else:
            room_count[second_room] = 1
        entry_list[11] = f"Room {room_count[second_room]} ({second_room})"

        table_data.append(entry_list)

    print(tabulate(table_data, headers=headers, tablefmt="grid", colalign=("center", "center", "center", "center", "center", "center", "center", "center", "center", "center", "center", "center", "center")))

print_solution(best_solution)
